In [ ]:
# ..... get cell types using Asp et al markers ..... #

In [2]:
library(SingleCellExperiment)
library(MetaMarkers)
library(Seurat)
library(data.table)
library(dplyr)

In [3]:
# load list of orthologs
om = read.delim('lizard_human_orthologs_eggNOG.txt', sep = '\t')
om <- om[!is.na(om$lizard_gene) & !is.na(om$ortholog_name),]
dim(om)
om[1,]

[1] 27011     7

query          orth_type species            orthologs       lizard_gene
1 XP_060608688.1 one2one   Homo sapiens(9606) ENSP00000340297 ARHGEF10   
  ortholog_gene   ortholog_name
1 ENSG00000104728 ARHGEF10

In [4]:
# list of stages and samples
stages = rep(c('stage9', 'stage13', 'stage16'), each = 3)
samples = paste0('sample', rep(1:3, 3))

In [5]:
# get top markers
get_top_markers <- function(df){
    ctypes = unique(df$cluster)
    marker_df = c()
    
    for(ii in 1:length(ctypes)){
        temp = df[df$cluster==ctypes[ii],]
        temp$group = 'all'
        temp$cell_type = temp$celltype
        
        if(dim(temp)[1]>100){
            marker_df = rbind(marker_df,
                              temp[1:100, c('group', 'cell_type', 'gene', 'avg_logFC', 'p_val_adj')])            
        }else{
            # take as many markers as possible
            marker_df = rbind(marker_df,
                              temp[, c('group', 'cell_type', 'gene', 'avg_logFC', 'p_val_adj')]) 
        }
    }
    return(as_tibble(marker_df))
}

In [6]:
# load markers
markers = read.delim('~/septation/markers/Asp/Asp_markers.csv', sep = ',')
markers$gene <- om$lizard_gene[match(markers$gene, om$ortholog_name)]
markers <- markers[!is.na(markers$gene),]
markers[1:2,]

# tibble of group, cell_type, gene, rank
top_markers = get_top_markers(markers)

p_val avg_logFC pct.1 pct.2 p_val_adj cluster gene  celltype             
1 0     2.168083  0.949 0.106 0         0       EMCN  Capillary endothelium
2 0     2.127456  0.967 0.136 0         0       PLVAP Capillary endothelium

In [10]:
# get cell type anno
pb = txtProgressBar(min = 0, max = length(samples), initial = 0)

for(id in 1:length(samples)){
    
    # load seurat object
    sce = readRDS(paste0(stages[id], '_', samples[id], '_data.rds'))

    # get SCE object
    sc3 = SingleCellExperiment(list(counts = LayerData(sce, assay = 'RNA', layer = 'counts')))
    colData(sc3) <- DataFrame(sce@meta.data)
    assay(sc3, "cpm") = convert_to_cpm(assay(sc3))
    
    # predict cell type neighborhood
    ct_scores = score_cells(log1p(cpm(sc3)), top_markers)
    ct_enrichment = compute_marker_enrichment(ct_scores)
    ct_pred = assign_cells(ct_scores)
    
    # save
    write.table(ct_pred, file = paste0('annotations/', stages[id], '_', samples[id], '_Asp_celltypes.csv'),
            sep = ',', row.names = T, col.names = T, quote = F)
    
    setTxtProgressBar(pb, id)
}